In [1]:
try:
    import sentence_transformers
except ImportError:
    !pip install sentence_transformers

try:
    import annoy
except ImportError:
    !pip install annoy

try:
    import datasets
except ImportError:
    !pip install datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 163.3/163.3 kB 3.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 31.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 47.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 66.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 2.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 8.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 13.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 MB 8.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.0/196.0 MB 6.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 166.0/166.0 MB 7.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.1/99.1 kB 12.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━

In [2]:
# imports
from sentence_transformers import SentenceTransformer
from annoy import AnnoyIndex
from sklearn.metrics.pairwise import cosine_similarity
from datasets import load_dataset

In [3]:
# 文章のベクトル化
def vectorize_sentences(sentences, model_name='sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2'):
    model = SentenceTransformer(model_name)
    return model.encode(sentences, show_progress_bar=True)

In [4]:
# Annoyインデックスの作成と類似文章の検索 + コサイン類似度に基づく重複判定
def build_and_search_annoy_index(vectors, n_trees=10, search_k=-1, threshold=0.8):
    f = vectors.shape[1]  # ベクトルの次元数
    annoy_index = AnnoyIndex(f, 'angular')

    for i, vector in enumerate(vectors):
        annoy_index.add_item(i, vector)

    annoy_index.build(n_trees)

    duplicate_indices = set()
    for i, vector in enumerate(vectors):
        nearest_indices = annoy_index.get_nns_by_item(i, 2, search_k=search_k)
        if i in nearest_indices:
            nearest_indices.remove(i)

        nearest_vector = vectors[nearest_indices[0]].reshape(1, -1)
        sim = cosine_similarity(vector.reshape(1, -1), nearest_vector)[0][0]
        if sim >= threshold:
            duplicate_indices.add(i)

    return duplicate_indices

# Wikipedia-jaで試してみる

2つのWikipediaデータセット間で重複検知できるか実験

In [5]:
# targetのデータセット
dataset = load_dataset("izumi-lab/wikipedia-ja-20230720", split="train[:100000]")

print("Size of dataset:", len(dataset))

dataset_features = list(dataset.features.keys())
print("Dataset features:", dataset_features)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Generating train split:   0%|          | 0/1362415 [00:00<?, ? examples/s]

Size of dataset: 100000
Dataset features: ['curid', 'title', 'text']


In [6]:
# queryのデータセット
dataset2 = load_dataset("mmnga/wikipedia-ja-20230720-2k", split="train")

print("Size of dataset:", len(dataset2))

dataset2_features = list(dataset2.features.keys())
print("Dataset features:", dataset2_features)

Generating train split:   0%|          | 0/2048 [00:00<?, ? examples/s]

Size of dataset: 2048
Dataset features: ['curid', 'title', 'text']


In [7]:
targets = [item['text'] for item in dataset]

# リストのサイズと最初の要素を表示
print("Size of text list:", len(targets))
print("First item of text list:", targets[0])

Size of text list: 100000
First item of text list: アンパサンド（&amp;, ）は、並立助詞「…と…」を意味する記号である。ラテン語で「…と…」を表す接続詞 "et" の合字を起源とする。現代のフォントでも、Trebuchet MS など一部のフォントでは、"et" の合字であることが容易にわかる字形を使用している。
語源.
英語で教育を行う学校でアルファベットを復唱する場合、その文字自体が単語となる文字（"A", "I", かつては " も）については、伝統的にラテン語の "（それ自体）を用いて "A per se A" のように唱えられていた。また、アルファベットの最後に、27番目の文字のように "&amp;" を加えることも広く行われていた。"&amp;" はラテン語で "et" と読まれていたが、後に英語で "and" と読まれるようになった。結果として、アルファベットの復唱の最後は "X, Y, Z, "and per se and"" という形になった。この最後のフレーズが繰り返されるうちに "ampersand" と訛っていき、この言葉は1837年までには英語の一般的な語法となった。
アンドレ＝マリ・アンペールがこの記号を自身の著作で使い、これが広く読まれたため、この記号が "Ampère's and" と呼ばれるようになったという誤った語源俗説がある。
歴史.
アンパサンドの起源は1世紀の古ローマ筆記体にまで遡ることができる。古ローマ筆記体では、E と T はしばしば合字として繋げて書かれていた（左図「アンパサンドの変遷」の字形1）。それに続く、流麗さを増した新ローマ筆記体では、様々な合字が極めて頻繁に使われるようになった。字形2と3は4世紀中頃における et の合字の例である。その後、9世紀のカロリング小文字体に至るラテン文字の変遷の過程で、合字の使用は一般には廃れていった。しかし、et の合字は使われ続け、次第に元の文字がわかりにくい字形に変化していった（字形4から6）。
現代のイタリック体のアンパサンドは、ルネサンス期に発展した筆記体での et の合字に遡る。1455年のヨーロッパにおける印刷技術の発明以降、印刷業者はイタリック体とローマ筆記体のアンパサンドの両方を多用するようになった。アンパ

In [8]:
queries = [item['text'] for item in dataset2]

# リストのサイズと最初の要素を表示
print("Size of text list:", len(queries))
print("First item of text list:", queries[0])

Size of text list: 2048
First item of text list: アルベルト・ポルトロニエリ(Alberto Poltronieri, 1892年11月9日 - 1983年1月13日)は、イタリアのヴァイオリニスト。
経歴.
ミラノ生まれ。ミラノ音楽院で学び、1923年から1950年までポルトロニエリ弦楽四重奏団を結成した。また、1930年からアルフレード・カゼッラとアルトゥーロ・ボヌッチとでピアノ三重奏団も結成し、1940年から1945年までの中断期を挟みつつ、1955年まで活動した。1949年には、コレギウム・ムジクム・イタリクムの創設に関わった。フェリーチェ・ラットゥアーダが1919年に作曲したヴァイオリン・ソナタはポルトロニエリに献呈されている。フランコ・マルゴーラが1948年に作曲したフルート四重奏曲もまた、アリーゴ・タッシナーリとポルトロニエリ弦楽四重奏団のために作られたものである。
公式記録とコンサート"live".
Quartetto Paganini.
"Alberto Poltronieri, violino / Osvaldo Scilla, viola / Roberto Caruana, violoncello / Guglielmo Papararo, chitarra"



In [9]:
%%time
# 文章の準備
sentences = [example['text'] for example in dataset] + [example['text'] for example in dataset2]

# 文章のベクトル化
vectors = vectorize_sentences(sentences)

# 重複の特定
duplicate_indices = build_and_search_annoy_index(vectors)

modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/122 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/4.12k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/645 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/9.08M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Batches:   0%|          | 0/3189 [00:00<?, ?it/s]

CPU times: user 12min 54s, sys: 5.74 s, total: 12min 59s
Wall time: 9min 41s


In [10]:
# 重複している文章の出力
print("重複していると特定された文章:")
for index in sorted(duplicate_indices):
    print(f'Index {index}: {sentences[index]}')

# 重複していない文章の抽出
unique_sentences = [sentence for i, sentence in enumerate(sentences) if i not in duplicate_indices]

print(f'元の文章数: {len(sentences)}')
print(f'重複除去後の文章数: {len(unique_sentences)}')

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Index 77856: 郡山町（こおりやまちょう）は、鹿児島県日置郡にあった町。
1889年（明治22年）に町村制が施行されたのに伴い郡山郷（外城）の区域を以て郡山村として発足。1956年9月30日に下伊集院村大字有屋田及び大字嶽を編入し、同時に町制施行。2004年11月1日、鹿児島市に編入され、自治体としては消滅した。
地理.
薩摩半島の中部に位置しており、町の中央部を北部にある甲突池を源流とする甲突川、西部を神之川、東部を川田川（甲突川支流）が流れ、流域に集落をそれぞれ形成している。
また北部は山岳地帯となっており、八重山をはじめとする500m級の山々が連なっている。
大字.
郡山町は2004年の鹿児島市編入の際には郡山、西俣、東俣、川田、油須木、厚地、有屋田、嶽の8大字から構成されていた。そのうち有屋田及び嶽の区域は1956年に下伊集院村の一部から分割された区域にあたる。
これらは現在の鹿児島市郡山町・西俣町・東俣町・川田町・油須木町・花尾町（旧大字厚地）・有屋田町・郡山岳町（旧大字嶽）にあたる。
学校.
小学校.
太字の学校は標準服がある。

Index 77861: ISSA

Index 77862: 壬生インターチェンジ（みぶインターチェンジ）は、栃木県下都賀郡壬生町大字国谷にある、北関東自動車道のインターチェンジ。下野市の旧下都賀郡石橋町域への最寄りとなるインターチェンジ。

Index 77867: 柏原本線料金所（かしわらほんせんりょうきんじょ）は、西名阪自動車道の柏原IC - 藤井寺IC間にある本線料金所である。
名古屋・天理方面から大阪方面に向かう車両について、香芝IC - 松原JCT間の均一料金を徴収する。
かつて、大阪方面行きの車両についても松原本線料金所で通行料金を徴収していたが、料金所のレーンが少なかったことにより渋滞が多発していた。その渋滞を緩和させるために、大阪行き車線については、1999年4月に当料金所を新設・移転し、供用を開始した。なお、現在の松原本線料金所については、全レーンが名古屋方面行きの車線専用としている。これにより、松原料金所付近の渋滞はほぼ解消された。
尚柏原本線料金所のブースを出た直後、左側の路肩側に同料金所事務所が有り、数台の駐車場とトイレが設置されている。

Index 77869: 九頭竜川（くずりゅう

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



元の文章数: 102048
重複除去後の文章数: 61134


In [11]:
%%time
# 文章の準備
sentences = [example['text'] for example in dataset] + [example['text'] for example in dataset2]

# 文章のベクトル化
vectors = vectorize_sentences(sentences)

# 重複の特定
duplicate_indices = build_and_search_annoy_index(vectors, 100)

Batches:   0%|          | 0/3189 [00:00<?, ?it/s]

CPU times: user 14min, sys: 4.33 s, total: 14min 4s
Wall time: 10min 24s


In [12]:
# 重複している文章の出力
print("重複していると特定された文章:")
for index in sorted(duplicate_indices):
    print(f'Index {index}: {sentences[index]}')

# 重複していない文章の抽出
unique_sentences = [sentence for i, sentence in enumerate(sentences) if i not in duplicate_indices]

print(f'元の文章数: {len(sentences)}')
print(f'重複除去後の文章数: {len(unique_sentences)}')

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Index 10934: 脚注.
注釈
出典

Index 10941: 声調（せいちょう）、またはトーン（）とは、言語において意味の区別に用いる音の高低のパターンである。声調を用いる言語を声調言語（トーン言語）という。
アクセントとの関係.
アクセントと声調は、ある語の中で高さの違いを示す特定の音節を指定する事で複数の型に分類可能であればアクセント、そうでなければ声調という区分けがなされる場合もある。しかし、アクセント言語と声調言語は明確に区別されるものではない。モイラ・イップは両者は声調の数と密度が異なるだけの連続体であるに過ぎず、アクセント言語は声調言語の下位区分であるとしている。イップの見解に従えば、日本語やセルビア・クロアチア語、オランダ語の一部といったアクセント言語も、広義の声調言語に含まれる事となる。
声調の種類.
日本語のように、単語中の特定の音節またはモーラでのみ高低の区別をするものについては、高低アクセントを参照。（ただし、日本にも西日本では広く単語声調が分布する。）
表記法.
国際音声記号による声調の表記.
国際音声記号(IPA)では次の2種類の方法で声調を表している。ダイアクリティカルマークを使う左側の方法はアフリカの声調言語の表記のためにとくにしばしば用いられてきた。右側の図像的な声調文字を後置させる方法は趙元任によって1933年に考案され、1989年にダイアクリティカルマークを使う方法と並んで国際音声記号として公式に採用された。右側の方法はタイ語や中国語のような言語に向いている。
平板
曲線
国際音声記号の一覧では両者の表示が1対1に対応するように書かれているが、これは表を単純化するためにこうなっているだけで、実際には両者は必ずしも対応しない。また、Unicodeでは声調文字を5種類(U+02E5 - U+02E9)しか定義していないが、複数の声調文字を並べることで曲折声調として表示されることになっている。
五度法（Five-level Scheme）.
上記の方法は、特殊な文字や記号を用意する必要があるが、記録や印刷が難しい場合、1から5の数字の組み合わせで表記することも行われている。趙元任によって創始された方法で、調値（tone value）、つまりピッチの高さを、1が一番低く、5が一番高いという5段階に分け、これを時間軸順に1つか

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Index 27595: 心斎橋駅（しんさいばしえき）は、大阪府大阪市中央区心斎橋筋一丁目にある、大阪市高速電気軌道 (Osaka Metro) の駅である。
御堂筋線と長堀鶴見緑地線が乗り入れるほか、改札内で四つ橋線の四ツ橋駅と連絡する。駅番号は御堂筋線の駅がM19、長堀鶴見緑地線の駅がN15。
駅構造.
御堂筋線・長堀鶴見緑地線ともに島式ホーム1面2線を有する地下駅である。戦前に開業した御堂筋線のホームは、淀屋橋駅などと同様にヴォールト構造である。長堀鶴見緑地線ホームの森ノ宮寄りには引き上げ線があり、京セラドーム大阪で野球やイベントが開催された際に運行される当駅止まり・当駅始発の臨時列車の折り返し、最終列車終了後に大正から回送される車両の夜間の留置（翌朝大正へ回送）などに使われる。
近隣の四つ橋線を含め、3線はコの字の形でつながっている。長堀鶴見緑地線ホームの森ノ宮寄りから御堂筋線ホームの梅田寄り、大正寄りから四つ橋線四ツ橋駅の西梅田寄りにつながっている構成である。長堀鶴見緑地線から四ツ橋駅までの間は距離があり、途中には構内および一般通路両方に動く歩道が設置されている。
また、長堀鶴見緑地線は御堂筋線や四つ橋線より下を通っているので、長堀鶴見緑地線心斎橋駅のホームはかなり深い位置にある。
当駅は、本町管区駅に所属し、駅長が配置されており、自駅のみの単駅管理となっている。
駅のデザインテーマ.
長堀鶴見緑地線の当駅のデザインテーマは「夕日と心斎橋」に設定されている。御堂筋線との乗り換え通路には、長堀川に架かっていた往時の心斎橋をモチーフとした装飾がなされている。
ただし、長堀鶴見緑地線・御堂筋線とも心斎橋の真下にホームはない。長堀鶴見緑地線ホームは二本西の佐野屋橋、御堂筋線ホームは一本西の新橋の真下あたりに位置している。実際の心斎橋は、御堂筋の東隣の筋の心斎橋筋（商店街）と長堀通の交点にある。なお、四ツ橋駅と心斎橋の間には、かつて大阪市電の停留所が四ツ橋・佐野屋橋・心斎橋と3つ設けられていた。
利用状況.
2022年11月15日の1日乗降人員は156,576人（乗車人員：75,515人、降車人員：81,061人）である。この数値には同一駅の四ツ橋駅も含まれている。
Osaka Metro全107駅中、梅田駅、なんば駅、天王寺駅、淀屋橋駅、本町駅に次いで6番目に多

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Index 86143: 鹿王院駅（ろくおういんえき）は、京都府京都市右京区嵯峨北堀町にある京福電気鉄道嵐山本線の停留場。駅ナンバリングはA11。
歴史.
路線開通当時は存在しなかった停留場で、公団住宅の建設を契機に開設された停留場である。そのため両停留場との距離が比較的短めとなっている。
停留場構造.
相対式ホーム各2面2線の地上駅。停留場東側の踏切を通過する道路へは各ホームとも階段で連絡する。
嵐山方面行きのホームの幅は特に狭く、ベンチは1人掛けのプラスチック製のものが2人分のみ設置されているが、ベンチ前の幅員を確保するためベンチの背もたれ部分をカットして設置している。なお、道路は踏切部分も含めて道幅が狭く、最も近い幹線道路である三条通への約300メートルの道程には自動車の離合が困難な場所がある。

Index 86145: 豊国（とよのくに、とよくに、古墳時代 - 7世紀）は、古墳時代にあった律令制以前の国の一つ。旧国名を豊日別（とよひわけ）と言い、現在の福岡県東部および大分県全域に相当する九州の北東部地域に存在した。律令制の時代には豊前国と豊後国に分かれた。
由来.
豊国は、『古事記』の国産み神話の中で、筑紫島（九州島）の4面のうちの一つで、当時は豊日別であったされる。
『日本書紀』や『先代旧事本紀』「天皇本紀」では景行天皇の皇子である豊国別皇子が日向国造の祖であると記す。『豊後国風土記』は豊国の国名の由来を次のように記す。
歴史.
旧石器・石器時代.
大分県大野郡の大野川流域にある上田原東遺跡（大分県豊後大野市）では、旧石器時代の遺物の出土がある。扁平打製石斧（石クワ）が多く出土し、稲作に関連する石包丁は出土していないため、当時は水田稲作ではなく、畑作を中心とした生業が営まれていたとみられている。
縄文・弥生時代.
縄文時代後期から弥生時代中期に竪穴建物や、花弁形の建物、土坑（貯蔵穴）が使用されていたことが分かっている。この時代は大野郡の陣箱遺跡の地域が発達した。
古墳時代.
大野郡の遺跡や、日田郡の小迫辻原遺跡（おざこ つじばる、日田市）の調査から、弥生時代終盤から古墳時代にかけて集落の移動があり、竪穴建物が方形になったことが分かっている。古墳時代の後半にはそうした住居に竈も作られるようになった。小迫辻原の環壕居館の遺構は、3世紀末から4世紀初頭のもの

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Index 94927: 柳瀬 尚紀（やなせ なおき、1943年3月2日 - 2016年7月30日）は、日本の英文学者、翻訳家、随筆家。
その翻訳は、語呂合わせなどの言葉遊びを駆使した独自の文体で、「悪訳」をするとみなした翻訳家に対する痛烈な批判を行っていた。
来歴・人物.
北海道根室市出身。1965年に早稲田大学第一文学部卒業、1967年同大学院文学研究科修士課程卒業、1970年同大学院文学研究科博士課程満期終了退学。1977年に成城大学助教授、1991年に辞職。
大学院時代、鈴木幸夫教授のグループでジョイスの翻訳を『早稲田文学』に連載していた。1976年にエリカ・ジョング『飛ぶのが怖い』の訳書がベストセラーとなり、「飛んでる女」が流行語となる。その後もジョング作品の翻訳を続けている。
高校時代までは数学者を志していた。ルイス・キャロルの翻訳も多く、数学に詳しい。ロングセラーとなった『シンデレラ・コンプレックス』の他にも、前衛的な文学を多数翻訳。英語・国語辞書や翻訳・国語論に関する著作も多い。
1981年に、第3回日本雑学大賞を受賞。
ジェイムズ・ジョイスの作品で、翻訳不可能と言われた『フィネガンズ・ウェイク』を独自の造語を用いて翻訳したことは話題となり、日本翻訳文化賞受賞、BABEL国際翻訳大賞・日本翻訳大賞受賞。『ジェイムズ・ジョイスの謎を解く』（岩波新書）では『ユリシーズ』12章の語り手が犬であるという新説を打ち出した。
『ユリシーズ』訳を継続中のまま、2016年7月30日に肺炎のため没したが、同年12月に『ユリシーズ 1 - 12』（12章まで）が刊行された。2017年7月に刊行された『ユリシーズ航海記 「ユリシーズ」を読むための本』（河出書房新社）には、「ユリシーズ 13 - 18　試訳と構想」という一章に、未刊に終わった第13章から18章の試訳（一部は断章）が掲載された。
趣味の領域を超えた活動も数多く、関連書籍も刊行した。
脚注.
[[Category:20世紀日本の翻訳家]]
[[Category:21世紀日本の翻訳家]]
[[Category:英語からの翻訳者]]
[[Category:日本の英語文学研究者]]
[[Category:イギリス文学者]]
[[Category:日本の児童文学研究者]]
[[Category:20世紀日本の随筆家]]

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [13]:
print(f'元の文章数: {len(sentences)}')
print(f'重複除去後の文章数: {len(unique_sentences)}')

元の文章数: 102048
重複除去後の文章数: 58220
